## Distributed training with Amazon SageMaker distributed libraries

This notebook demonstrates usage of smdistributed dataparallel and smdistributed modelparallel libraries.

Note that the focus is not on coming up with the best performing model, but to understand the training time improvements using the distributed libraries provided by SageMaker.

### Overview

1. Set up
2. Establish a baseline with PyTorch model training without distributed training enabled.
3. Train PyTorch model with dataparallel enabled.
4. Train PyTorch model with modelparallel enabled.

#### 1. Set up

#### 1.1 Imports

In [1]:
import sagemaker
import boto3
from sagemaker import image_uris
from sagemaker.session import Session
from sagemaker.inputs import TrainingInput

from sagemaker.pytorch import PyTorch

#### 1.2 Setup variables

In [2]:
#Set the s3_bucket to the correct bucket name created in your datascience environment
s3_bucket = 'datascience-environment-notebookinstance--06dc7a0224df'
s3_prefix = 'prepared'

sagemaker_session = sagemaker.Session()
region = sagemaker_session.boto_region_name

#### 1.3 Setup service clients

In [3]:
#Create the service clients
s3_client = boto3.client('s3', region_name=region)

#### 1.4 Setup training and validation files

In [4]:
##Get the file name at index from the 'prefix' folder
def get_file_in_bucket(prefix,index):
    response = s3_client.list_objects(
        Bucket=s3_bucket,
        Prefix=s3_prefix + "/" + prefix
    )
    ## At '0' index you will find the SUCCESS/FAILURE of file uploades to S3. First data file is at index 1
    file_name = response['Contents'][index]['Key']
    print("Returing file name : " + file_name)
    return file_name

In [5]:
#Different train and validation inputs
#Define the data type and paths to the training and validation datasets
content_type = "csv"

#Since we are using powerful CPU/GPU instances for training over hours, you can choose to use a single file 
#for training and validation instead of the entrie dataset to save some time and trainging costs.  
    
train_input_single_file = TrainingInput("s3://{}/{}".format(s3_bucket, get_file_in_bucket('train',1)))
validation_input_single_file = TrainingInput("s3://{}/{}".format(s3_bucket, get_file_in_bucket('validation',1)))

train_input = TrainingInput("s3://{}/{}/{}/".format(s3_bucket, s3_prefix, 'train'), content_type=content_type, distribution='ShardedByS3Key')
validation_input = TrainingInput("s3://{}/{}/{}/".format(s3_bucket, s3_prefix, 'validation'), content_type=content_type, distribution='ShardedByS3Key')

Returing file name : prepared/train/part-00000-2554f113-947e-46bd-be31-9cd75cb4661c-c000.csv
Returing file name : prepared/validation/part-00000-85addac2-a753-4bc2-b157-26ff8f5d5952-c000.csv


In [6]:
##Please check your AWS account limits, to make sure you have access to the training infrastructure (both type and count).
##If necessary you can increase your instance limits by filing a support ticket.

#Training instance type
train_instance_type = "ml.p3.16xlarge"
#Training instance count
train_instance_count = 1

### 2. Establish a baseline with PyTorch model training without distributed training enabled

We will first create a baseline by building a PyTorch model without any distributed training.

Note that we use a simple CSV data loader that reads the entire data set into memory. If that proves infeasible, consider using a more sophisticated CSV loader or a [Redis-based loader](https://github.com/RedisAI/RedisAI).


In [18]:
pt_estimator_no_dist = PyTorch(
    entry_point="train_pytorch.py",
    source_dir="../code",
    role=sagemaker.get_execution_role(),
    instance_count=train_instance_count,
    instance_type=train_instance_type,
    framework_version="1.8.1",
    py_version="py3",
    volume_size=1024
)

In [19]:
#Let's do a quick check with a single train and validation file first
##This step takes about 22 minutes.
pt_estimator_no_dist.fit({'train': train_input_single_file, 'test': validation_input_single_file})

2021-08-08 01:44:16 Starting - Starting the training job...
2021-08-08 01:44:39 Starting - Launching requested ML instancesProfilerReport-1628387055: InProgress
.........
2021-08-08 01:46:12 Starting - Preparing the instances for training.........
2021-08-08 01:47:42 Downloading - Downloading input data...
2021-08-08 01:48:00 Training - Downloading the training image.......................bash: cannot set terminal process group (-1): Inappropriate ioctl for device
bash: no job control in this shell
2021-08-08 01:52:00,141 sagemaker-training-toolkit INFO     Imported framework sagemaker_pytorch_container.training
2021-08-08 01:52:00,218 sagemaker_pytorch_container.training INFO     Block until all host DNS lookups succeed.
2021-08-08 01:52:03,265 sagemaker_pytorch_container.training INFO     Invoking user training script.
2021-08-08 01:52:03,898 sagemaker-training-toolkit INFO     Invoking user script

Training Env:

{
    "additional_framework_parameters": {},
    "channel_input_dirs":

In [ ]:
#Now let's train on the full training set.
pt_estimator_no_dist.fit({'train': train_input, 'test': validation_input})

2021-08-07 18:08:31 Starting - Starting the training job...
2021-08-07 18:08:54 Starting - Launching requested ML instancesProfilerReport-1628359710: InProgress
.........
2021-08-07 18:10:14 Starting - Preparing the instances for training.........
2021-08-07 18:11:54 Downloading - Downloading input data...............
2021-08-07 18:14:27 Training - Training image download completed. Training in progress..bash: cannot set terminal process group (-1): Inappropriate ioctl for device
bash: no job control in this shell
2021-08-07 18:14:28,077 sagemaker-training-toolkit INFO     Imported framework sagemaker_pytorch_container.training
2021-08-07 18:14:28,154 sagemaker_pytorch_container.training INFO     Block until all host DNS lookups succeed.
2021-08-07 18:14:28,162 sagemaker_pytorch_container.training INFO     Invoking user training script.
2021-08-07 18:14:28,853 sagemaker-training-toolkit INFO     Invoking user script

Training Env:

{
    "additional_framework_parameters": {},
    "chan

For the baseline, PyTorch training without any distributed training gives us a training time of 11005 seconds and Test MSE of 2.2653368432656862e-05.  Note that your results may be different.

Now let's see if we can improve on this using dataparallel distributed library.

### 3. PyTorch model training on a single instance with dataparallel library

In [12]:
##Note that we are using a different pytorch script here. Please review the train_pytorch_dist.py files for changes necessary to support dataparallel
pt_estimator_dist = PyTorch(
    entry_point="train_pytorch_dist.py",
    source_dir="../code",
    role=sagemaker.get_execution_role(),
    instance_count=train_instance_count,
    instance_type=train_instance_type,
    framework_version="1.8.1",
    py_version="py36",
    volume_size=256,
    ##Enable data parallellism
    distribution={"smdistributed": {"dataparallel": {"enabled": True}}},
    debugger_hook_config=False,
    disable_profiler=True
)

In [13]:
#Uncomment if you want to test with a single training and validation file
#This step roughly takes about 12 minutes , with 549 seconds of training time and gives a test MSE of 0.921
pt_estimator_dist.fit({'train': train_input_single_file, 'test': validation_input_single_file})

2021-08-07 22:23:35 Starting - Starting the training job...
2021-08-07 22:23:36 Starting - Launching requested ML instances.........
2021-08-07 22:25:12 Starting - Preparing the instances for training.........
2021-08-07 22:26:52 Downloading - Downloading input data
2021-08-07 22:26:52 Training - Downloading the training image.........................bash: cannot set terminal process group (-1): Inappropriate ioctl for device
bash: no job control in this shell
2021-08-07 22:31:02,732 sagemaker-training-toolkit INFO     Imported framework sagemaker_pytorch_container.training
2021-08-07 22:31:02,809 sagemaker_pytorch_container.training INFO     Block until all host DNS lookups succeed.
2021-08-07 22:31:02,817 sagemaker_pytorch_container.training INFO     Invoking SMDataParallel
2021-08-07 22:31:02,817 sagemaker_pytorch_container.training INFO     Invoking user training script.
2021-08-07 22:31:03,317 sagemaker-training-toolkit INFO     Starting MPI run as worker node.
2021-08-07 22:31:03

In [14]:
#Now let's train on the full training set.
pt_estimator_dist.fit({'train': train_input, 'test': validation_input})

2021-08-07 22:35:53 Starting - Starting the training job...
2021-08-07 22:35:54 Starting - Launching requested ML instances.........
2021-08-07 22:37:50 Starting - Preparing the instances for training.........
2021-08-07 22:39:22 Downloading - Downloading input data..................
2021-08-07 22:42:01 Training - Downloading the training image...
2021-08-07 22:42:46 Training - Training image download completed. Training in progress.bash: cannot set terminal process group (-1): Inappropriate ioctl for device
bash: no job control in this shell
2021-08-07 22:42:47,538 sagemaker-training-toolkit INFO     Imported framework sagemaker_pytorch_container.training
2021-08-07 22:42:47,617 sagemaker_pytorch_container.training INFO     Block until all host DNS lookups succeed.
2021-08-07 22:42:53,869 sagemaker_pytorch_container.training INFO     Invoking SMDataParallel
2021-08-07 22:42:53,869 sagemaker_pytorch_container.training INFO     Invoking user training script.
2021-08-07 22:42:54,472 sage

##### Compare against the baseline

Data parallelism gives us a Test MSE of 0.03 with a time of 3675 seconds.  Compared to 11005 seconds without distributed training, that's a 66.6% speedup.

### 4. PyTorch model training on a single instance with modelparallel library

In [15]:
mpi_options = {
    "enabled": True,
   "processes_per_host": 4
}
  
dist_options = {
    "modelparallel":{
       "enabled": True,
       "parameters": {
           "partitions": 4,  # we'll partition the model among the 4 GPUs 
           "microbatches": 8,  # Mini-batchs are split in micro-batch to increase parallelism
           "optimize": "memory" # The automatic model partitioning can optimize speed or memory
           }
       }
}

In [16]:
pt_model_dist_estimator = PyTorch(
    entry_point="train_pytorch_model_dist.py",
    source_dir="../code",
    role=sagemaker.get_execution_role(),
    instance_count=1,
    instance_type="ml.p3.8xlarge",
    framework_version="1.8.1",
    py_version="py36",
    volume_size=256,
    distribution={"mpi": mpi_options, "smdistributed": dist_options}
)

#### CAUTION Executing the distributed training with model parallelism with the complete dataset took over 20 hours.  Yikes!!!  To show the usage, the following just uses a single file that takes about 2 hours. 

#### If you like to train with the complete dataset, uncomment the below and run the fit job. Please note this will be a costly experiment :) 

In [17]:
#This step, training with a single file, roughly takes about 90 minutes
pt_model_dist_estimator.fit({'train': train_input_single_file, 'test': validation_input_single_file})
#Train with full dataset.
#pt_model_dist_estimator.fit({'train': train_input, 'test': validation_input})

2021-08-07 23:45:01 Starting - Starting the training job...
2021-08-07 23:45:24 Starting - Launching requested ML instancesProfilerReport-1628379901: InProgress
.........
2021-08-07 23:46:45 Starting - Preparing the instances for training......
2021-08-07 23:48:00 Downloading - Downloading input data
2021-08-07 23:48:00 Training - Downloading the training image......................bash: cannot set terminal process group (-1): Inappropriate ioctl for device
bash: no job control in this shell
2021-08-07 23:51:37,704 sagemaker-training-toolkit INFO     Imported framework sagemaker_pytorch_container.training
2021-08-07 23:51:37,747 sagemaker_pytorch_container.training INFO     Block until all host DNS lookups succeed.
2021-08-07 23:51:37,755 sagemaker_pytorch_container.training INFO     Invoking user training script.
2021-08-07 23:51:38,149 sagemaker-training-toolkit INFO     Starting MPI run as worker node.
2021-08-07 23:51:38,150 sagemaker-training-toolkit INFO     Creating SSH daemon.


##### Compare against the baseline and data parallelism

With model parallelism enabled, the training job with the full dataset runs for over 20 hours, which indicates that in this case this is not the appropriate strategy.  However it would be good to know  what is going on during those 20 hours.  Could there be any configurtion settings that can be changed to get better results?  In the next chapter, you will see how to use SageMaker debugger to gain insight into a running training job.